# Fake News Classification using ML

In [14]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import nltk
import re
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer

from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.preprocessing.text import one_hot
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.layers import Embedding
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense
from tensorflow.keras.models import Sequential

In [2]:
news_data = pd.read_csv("data/news-dataset.csv")
news_data.head()

index                                              title  \
0      0  PRESIDENT TRUMP Explains New “America First” R...   
1      1  TERMINALLY ILL FORMER MISS WI: “Until my last ...   
2      2   Cruz Humiliated By Moderator After Lie About ...   
3      3  Russia revels in Trump victory, looks to sanct...   
4      4  Trump's bid to open U.S. monuments to developm...   

                                                text       subject  \
0  That s what we re talking about! Another campa...      politics   
1  How is it that Sean Hannity is the only media ...      politics   
2  Almost immediately after learning that longtim...          News   
3  MOSCOW (Reuters) - For all their mutual praise...  politicsNews   
4  WASHINGTON (Reuters) - The Trump administratio...  politicsNews   

                date class  Unnamed: 6  
0        Aug 2, 2017  Fake         NaN  
1        Oct 4, 2016  Fake         NaN  
2  February 13, 2016  Fake         NaN  
3  November 9, 2016   Real         NaN  
4      May 26, 2017   Real         NaN

In [3]:
news_data.shape

(40000, 7)

## Cleaning the dataset

In [4]:
news_data.drop(columns=["index", "subject", "date", "Unnamed: 6"], 
               inplace = True)

In [5]:
news_data = news_data.dropna()
news_data.reset_index(inplace = True)
news_data.head()

index                                              title  \
0      0  PRESIDENT TRUMP Explains New “America First” R...   
1      1  TERMINALLY ILL FORMER MISS WI: “Until my last ...   
2      2   Cruz Humiliated By Moderator After Lie About ...   
3      3  Russia revels in Trump victory, looks to sanct...   
4      4  Trump's bid to open U.S. monuments to developm...   

                                                text class  
0  That s what we re talking about! Another campa...  Fake  
1  How is it that Sean Hannity is the only media ...  Fake  
2  Almost immediately after learning that longtim...  Fake  
3  MOSCOW (Reuters) - For all their mutual praise...  Real  
4  WASHINGTON (Reuters) - The Trump administratio...  Real

In [6]:
# Checking for any null values
news_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 40000 entries, 0 to 39999
Data columns (total 4 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   index   40000 non-null  int64 
 1   title   40000 non-null  object
 2   text    40000 non-null  object
 3   class   40000 non-null  object
dtypes: int64(1), object(3)
memory usage: 1.2+ MB


In [7]:
news_data.shape

(40000, 4)

## Independent and Dependent Features

In [8]:
# We are only using 'title' as an independent feature
X = news_data.iloc[:, 2]
y = news_data.iloc[:, 3]

X.shape, y.shape

((40000,), (40000,))

## Text Preprocessing

In [9]:
# Giving numerical representation to labels
y = pd.get_dummies(y)
y.head()

Fake  Real
0     1     0
1     1     0
2     1     0
3     0     1
4     0     1

In [10]:
y = y.iloc[:, 0]
y

0        1
1        1
2        1
3        0
4        0
        ..
39995    0
39996    1
39997    1
39998    1
39999    0
Name: Fake, Length: 40000, dtype: uint8

In [11]:
# In part-2, we are using texts instead of titles
X[8]

'DETROIT (Reuters) - The list of priorities U.S. Trade Representative Robert Lighthizer released this week for the renegotiation of NAFTA with Mexico and Canada is reasonable and in line with what the Trump administration has promised to focus on, the head of America’s largest railroad said on Thursday.  “It was a very reasonable document,” Union Pacific Corp (UNP.N) Chief Executive Lance Fritz said in an interview about a list of priorities released this week by Lighthizer. “From our perspective, he (Lighthizer) hit all of the elements that we’ve heard from the administration and they make sense.” Republican U.S. President Donald Trump has threatened to exit the North American Free Trade Agreement if it is not renegotiated in favor of the United States. Talks with Mexico and Canada on revisions to the treaty, which came into effect in 1994, are due to start in mid-August.  The top priority for the talks listed by Lighthizer’s office was shrinking the U.S. trade deficit with Canada and

In [12]:
# Stemming the data
stemmer = PorterStemmer()
corpus = []

for i in range(len(X)):
    print("At sentence: {}".format(i))
    
    review = re.sub("[^a-zA-Z]", " ", X[i])
    review = review.lower()
    review = review.split()
    
    review = [stemmer.stem(word) for word in review if not word in set(stopwords.words("english"))]
    review = ' '.join(review)
    corpus.append(review)

At sentence: 0
At sentence: 1
At sentence: 2
At sentence: 3
At sentence: 4
At sentence: 5
At sentence: 6
At sentence: 7
At sentence: 8
At sentence: 9
At sentence: 10
At sentence: 11
At sentence: 12
At sentence: 13
At sentence: 14
At sentence: 15
At sentence: 16
At sentence: 17
At sentence: 18
At sentence: 19
At sentence: 20
At sentence: 21
At sentence: 22
At sentence: 23
At sentence: 24
At sentence: 25
At sentence: 26
At sentence: 27
At sentence: 28
At sentence: 29
At sentence: 30
At sentence: 31
At sentence: 32
At sentence: 33
At sentence: 34
At sentence: 35
At sentence: 36
At sentence: 37
At sentence: 38
At sentence: 39
At sentence: 40
At sentence: 41
At sentence: 42
At sentence: 43
At sentence: 44
At sentence: 45
At sentence: 46
At sentence: 47
At sentence: 48
At sentence: 49
At sentence: 50
At sentence: 51
At sentence: 52
At sentence: 53
At sentence: 54
At sentence: 55
At sentence: 56
At sentence: 57
At sentence: 58
At sentence: 59
At sentence: 60
At sentence: 61
At sentence: 62
At

At sentence: 489
At sentence: 490
At sentence: 491
At sentence: 492
At sentence: 493
At sentence: 494
At sentence: 495
At sentence: 496
At sentence: 497
At sentence: 498
At sentence: 499
At sentence: 500
At sentence: 501
At sentence: 502
At sentence: 503
At sentence: 504
At sentence: 505
At sentence: 506
At sentence: 507
At sentence: 508
At sentence: 509
At sentence: 510
At sentence: 511
At sentence: 512
At sentence: 513
At sentence: 514
At sentence: 515
At sentence: 516
At sentence: 517
At sentence: 518
At sentence: 519
At sentence: 520
At sentence: 521
At sentence: 522
At sentence: 523
At sentence: 524
At sentence: 525
At sentence: 526
At sentence: 527
At sentence: 528
At sentence: 529
At sentence: 530
At sentence: 531
At sentence: 532
At sentence: 533
At sentence: 534
At sentence: 535
At sentence: 536
At sentence: 537
At sentence: 538
At sentence: 539
At sentence: 540
At sentence: 541
At sentence: 542
At sentence: 543
At sentence: 544
At sentence: 545
At sentence: 546
At sentence: 5

At sentence: 973
At sentence: 974
At sentence: 975
At sentence: 976
At sentence: 977
At sentence: 978
At sentence: 979
At sentence: 980
At sentence: 981
At sentence: 982
At sentence: 983
At sentence: 984
At sentence: 985
At sentence: 986
At sentence: 987
At sentence: 988
At sentence: 989
At sentence: 990
At sentence: 991
At sentence: 992
At sentence: 993
At sentence: 994
At sentence: 995
At sentence: 996
At sentence: 997
At sentence: 998
At sentence: 999
At sentence: 1000
At sentence: 1001
At sentence: 1002
At sentence: 1003
At sentence: 1004
At sentence: 1005
At sentence: 1006
At sentence: 1007
At sentence: 1008
At sentence: 1009
At sentence: 1010
At sentence: 1011
At sentence: 1012
At sentence: 1013
At sentence: 1014
At sentence: 1015
At sentence: 1016
At sentence: 1017
At sentence: 1018
At sentence: 1019
At sentence: 1020
At sentence: 1021
At sentence: 1022
At sentence: 1023
At sentence: 1024
At sentence: 1025
At sentence: 1026
At sentence: 1027
At sentence: 1028
At sentence: 1029
A

At sentence: 1431
At sentence: 1432
At sentence: 1433
At sentence: 1434
At sentence: 1435
At sentence: 1436
At sentence: 1437
At sentence: 1438
At sentence: 1439
At sentence: 1440
At sentence: 1441
At sentence: 1442
At sentence: 1443
At sentence: 1444
At sentence: 1445
At sentence: 1446
At sentence: 1447
At sentence: 1448
At sentence: 1449
At sentence: 1450
At sentence: 1451
At sentence: 1452
At sentence: 1453
At sentence: 1454
At sentence: 1455
At sentence: 1456
At sentence: 1457
At sentence: 1458
At sentence: 1459
At sentence: 1460
At sentence: 1461
At sentence: 1462
At sentence: 1463
At sentence: 1464
At sentence: 1465
At sentence: 1466
At sentence: 1467
At sentence: 1468
At sentence: 1469
At sentence: 1470
At sentence: 1471
At sentence: 1472
At sentence: 1473
At sentence: 1474
At sentence: 1475
At sentence: 1476
At sentence: 1477
At sentence: 1478
At sentence: 1479
At sentence: 1480
At sentence: 1481
At sentence: 1482
At sentence: 1483
At sentence: 1484
At sentence: 1485
At sentenc

At sentence: 1887
At sentence: 1888
At sentence: 1889
At sentence: 1890
At sentence: 1891
At sentence: 1892
At sentence: 1893
At sentence: 1894
At sentence: 1895
At sentence: 1896
At sentence: 1897
At sentence: 1898
At sentence: 1899
At sentence: 1900
At sentence: 1901
At sentence: 1902
At sentence: 1903
At sentence: 1904
At sentence: 1905
At sentence: 1906
At sentence: 1907
At sentence: 1908
At sentence: 1909
At sentence: 1910
At sentence: 1911
At sentence: 1912
At sentence: 1913
At sentence: 1914
At sentence: 1915
At sentence: 1916
At sentence: 1917
At sentence: 1918
At sentence: 1919
At sentence: 1920
At sentence: 1921
At sentence: 1922
At sentence: 1923
At sentence: 1924
At sentence: 1925
At sentence: 1926
At sentence: 1927
At sentence: 1928
At sentence: 1929
At sentence: 1930
At sentence: 1931
At sentence: 1932
At sentence: 1933
At sentence: 1934
At sentence: 1935
At sentence: 1936
At sentence: 1937
At sentence: 1938
At sentence: 1939
At sentence: 1940
At sentence: 1941
At sentenc

...

At sentence: 38227
At sentence: 38228
At sentence: 38229
At sentence: 38230
At sentence: 38231
At sentence: 38232
At sentence: 38233
At sentence: 38234
At sentence: 38235
At sentence: 38236
At sentence: 38237
At sentence: 38238
At sentence: 38239
At sentence: 38240
At sentence: 38241
At sentence: 38242
At sentence: 38243
At sentence: 38244
At sentence: 38245
At sentence: 38246
At sentence: 38247
At sentence: 38248
At sentence: 38249
At sentence: 38250
At sentence: 38251
At sentence: 38252
At sentence: 38253
At sentence: 38254
At sentence: 38255
At sentence: 38256
At sentence: 38257
At sentence: 38258
At sentence: 38259
At sentence: 38260
At sentence: 38261
At sentence: 38262
At sentence: 38263
At sentence: 38264
At sentence: 38265
At sentence: 38266
At sentence: 38267
At sentence: 38268
At sentence: 38269
At sentence: 38270
At sentence: 38271
At sentence: 38272
At sentence: 38273
At sentence: 38274
At sentence: 38275
At sentence: 38276
At sentence: 38277
At sentence: 38278
At sentence:

At sentence: 38660
At sentence: 38661
At sentence: 38662
At sentence: 38663
At sentence: 38664
At sentence: 38665
At sentence: 38666
At sentence: 38667
At sentence: 38668
At sentence: 38669
At sentence: 38670
At sentence: 38671
At sentence: 38672
At sentence: 38673
At sentence: 38674
At sentence: 38675
At sentence: 38676
At sentence: 38677
At sentence: 38678
At sentence: 38679
At sentence: 38680
At sentence: 38681
At sentence: 38682
At sentence: 38683
At sentence: 38684
At sentence: 38685
At sentence: 38686
At sentence: 38687
At sentence: 38688
At sentence: 38689
At sentence: 38690
At sentence: 38691
At sentence: 38692
At sentence: 38693
At sentence: 38694
At sentence: 38695
At sentence: 38696
At sentence: 38697
At sentence: 38698
At sentence: 38699
At sentence: 38700
At sentence: 38701
At sentence: 38702
At sentence: 38703
At sentence: 38704
At sentence: 38705
At sentence: 38706
At sentence: 38707
At sentence: 38708
At sentence: 38709
At sentence: 38710
At sentence: 38711
At sentence:

At sentence: 39093
At sentence: 39094
At sentence: 39095
At sentence: 39096
At sentence: 39097
At sentence: 39098
At sentence: 39099
At sentence: 39100
At sentence: 39101
At sentence: 39102
At sentence: 39103
At sentence: 39104
At sentence: 39105
At sentence: 39106
At sentence: 39107
At sentence: 39108
At sentence: 39109
At sentence: 39110
At sentence: 39111
At sentence: 39112
At sentence: 39113
At sentence: 39114
At sentence: 39115
At sentence: 39116
At sentence: 39117
At sentence: 39118
At sentence: 39119
At sentence: 39120
At sentence: 39121
At sentence: 39122
At sentence: 39123
At sentence: 39124
At sentence: 39125
At sentence: 39126
At sentence: 39127
At sentence: 39128
At sentence: 39129
At sentence: 39130
At sentence: 39131
At sentence: 39132
At sentence: 39133
At sentence: 39134
At sentence: 39135
At sentence: 39136
At sentence: 39137
At sentence: 39138
At sentence: 39139
At sentence: 39140
At sentence: 39141
At sentence: 39142
At sentence: 39143
At sentence: 39144
At sentence:

At sentence: 39526
At sentence: 39527
At sentence: 39528
At sentence: 39529
At sentence: 39530
At sentence: 39531
At sentence: 39532
At sentence: 39533
At sentence: 39534
At sentence: 39535
At sentence: 39536
At sentence: 39537
At sentence: 39538
At sentence: 39539
At sentence: 39540
At sentence: 39541
At sentence: 39542
At sentence: 39543
At sentence: 39544
At sentence: 39545
At sentence: 39546
At sentence: 39547
At sentence: 39548
At sentence: 39549
At sentence: 39550
At sentence: 39551
At sentence: 39552
At sentence: 39553
At sentence: 39554
At sentence: 39555
At sentence: 39556
At sentence: 39557
At sentence: 39558
At sentence: 39559
At sentence: 39560
At sentence: 39561
At sentence: 39562
At sentence: 39563
At sentence: 39564
At sentence: 39565
At sentence: 39566
At sentence: 39567
At sentence: 39568
At sentence: 39569
At sentence: 39570
At sentence: 39571
At sentence: 39572
At sentence: 39573
At sentence: 39574
At sentence: 39575
At sentence: 39576
At sentence: 39577
At sentence:

At sentence: 39958
At sentence: 39959
At sentence: 39960
At sentence: 39961
At sentence: 39962
At sentence: 39963
At sentence: 39964
At sentence: 39965
At sentence: 39966
At sentence: 39967
At sentence: 39968
At sentence: 39969
At sentence: 39970
At sentence: 39971
At sentence: 39972
At sentence: 39973
At sentence: 39974
At sentence: 39975
At sentence: 39976
At sentence: 39977
At sentence: 39978
At sentence: 39979
At sentence: 39980
At sentence: 39981
At sentence: 39982
At sentence: 39983
At sentence: 39984
At sentence: 39985
At sentence: 39986
At sentence: 39987
At sentence: 39988
At sentence: 39989
At sentence: 39990
At sentence: 39991
At sentence: 39992
At sentence: 39993
At sentence: 39994
At sentence: 39995
At sentence: 39996
At sentence: 39997
At sentence: 39998
At sentence: 39999


In [13]:
corpus[8]

'detroit reuter list prioriti u trade repres robert lighthiz releas week renegoti nafta mexico canada reason line trump administr promis focu head america largest railroad said thursday reason document union pacif corp unp n chief execut lanc fritz said interview list prioriti releas week lighthiz perspect lighthiz hit element heard administr make sens republican u presid donald trump threaten exit north american free trade agreement renegoti favor unit state talk mexico canada revis treati came effect due start mid august top prioriti talk list lighthiz offic shrink u trade deficit canada mexico union pacif fritz said lighthiz focu intellectu properti labor law disput resolut mechan make sens make sens us element lighthiz prioriti focus streamlin freight across border ad percent union pacif freight volum base intern trade percent base cross border trade mexico fritz said mexico continu good driver union pacif growth ceo spoke reuter union pacif post better expect second quarter profit

## Creating One-hot representations

In [15]:
# Defining vocabulary size
vocab_size = 15000

In [16]:
onehot_representation = [one_hot(words, vocab_size) for words in corpus]
onehot_representation

[[3928,
  1823,
  12092,
  8212,
  12105,
  14314,
  6356,
  12763,
  14522,
  5288,
  10282,
  10145,
  10213,
  14924,
  4139,
  4233,
  917,
  8212,
  12333,
  11537,
  6466,
  3878,
  12323,
  1504,
  10282,
  10145,
  4014,
  4997,
  9821,
  9892,
  6390,
  4429,
  11472,
  582,
  3896,
  4586,
  10423,
  895,
  9109,
  9741,
  11884,
  150,
  13976,
  10307,
  11840,
  2585,
  8533,
  4113,
  12349,
  1747,
  10282,
  895,
  1349,
  12211,
  4586,
  11884,
  13879,
  2644,
  13062,
  12092,
  3950,
  9109,
  9741,
  4586,
  11884,
  589,
  10580,
  9044,
  601,
  12968,
  10145,
  7502,
  4014,
  12334,
  442,
  2389,
  7961,
  937,
  442,
  2081,
  3645,
  9821,
  10226,
  9289,
  12211,
  11537,
  4586,
  12269,
  3436,
  14269,
  1512,
  5151,
  7502,
  11472,
  8434,
  2969,
  6318,
  8904,
  3949,
  2711,
  13879,
  1298,
  8817,
  10145,
  7961,
  3645,
  8245,
  14482,
  5538,
  10114,
  4737,
  4586,
  4192,
  4585,
  1052,
  4974,
  8819,
  724,
  10646,
  524,
  11137,


In [17]:
find_max = []
for sentences in corpus:
    find_max.append(len(sentences.split()))

In [21]:
# Finding the length of sentences in corpus at 99th percentile 
np.percentile(find_max, 99.9)

2371.0030000000115

## Word Embeddings - Feature Representation

In [22]:
sentence_length = 1500
embedded_docs = pad_sequences(onehot_representation, 
                              padding = "pre", 
                              maxlen = sentence_length)

embedded_docs

array([[    0,     0,     0, ...,  2212, 10018, 12145],
       [    0,     0,     0, ...,  7047,  4113, 13849],
       [    0,     0,     0, ...,  9288,  5721, 12145],
       ...,
       [    0,     0,     0, ...,  6356, 13636,  9198],
       [    0,     0,     0, ...,  3884, 10135,  1577],
       [    0,     0,     0, ...,  2996,  9653, 14685]])

In [24]:
len(embedded_docs), y.shape

(40000, (40000,))

In [25]:
X_final = np.array(embedded_docs)
y_final = np.array(y)

In [26]:
X_final.shape, y_final.shape

((40000, 1500), (40000,))

In [27]:
X_train, X_test, y_train, y_test = train_test_split(X_final, y_final, 
                                                    test_size = 0.33, 
                                                    random_state = 0)

X_train.shape, X_test.shape, y_train.shape, y_test.shape

((26800, 1500), (13200, 1500), (26800,), (13200,))

## Creating the Model

In [29]:
embedding_vector_features = 200

model = Sequential()
model.add(Embedding(vocab_size,
                    embedding_vector_features,
                    input_length = sentence_length))

model.add(LSTM(units = 128,
               return_sequences = True,
               dropout = 0.3))

model.add(LSTM(units = 64,
               dropout = 0.15))

model.add(Dense(units = 32,
                activation = "relu"))

model.add(Dense(1,
                activation = "sigmoid"))

In [30]:
model.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_1 (Embedding)     (None, 1500, 200)         3000000   
                                                                 
 lstm_2 (LSTM)               (None, 1500, 128)         168448    
                                                                 
 lstm_3 (LSTM)               (None, 64)                49408     
                                                                 
 dense (Dense)               (None, 32)                2080      
                                                                 
 dense_1 (Dense)             (None, 1)                 33        
                                                                 
Total params: 3,219,969
Trainable params: 3,219,969
Non-trainable params: 0
_________________________________________________________________


In [31]:
model.compile(
        optimizer = "adam", 
        loss = "binary_crossentropy", 
        metrics = ["accuracy"]
)

In [32]:
# Creating a checkpoint for model
checkpoint_cb = tf.keras.callbacks.ModelCheckpoint("Best_model_LSTM.h5", save_best_only = True)

In [ ]:
model.fit(X_train, y_train, 
         validation_data = (X_test, y_test), 
         epochs = 15, 
         batch_size = 64, 
         callbacks = [checkpoint_cb])

Epoch 1/15
419/419 [==============================] - 159s 359ms/step - loss: 0.1494 - accuracy: 0.9457 - val_loss: 0.0703 - val_accuracy: 0.9798
Epoch 2/15
419/419 [==============================] - 151s 359ms/step - loss: 0.0558 - accuracy: 0.9809 - val_loss: 0.0425 - val_accuracy: 0.9864
Epoch 3/15
419/419 [==============================] - 150s 358ms/step - loss: 0.0418 - accuracy: 0.9873 - val_loss: 0.0534 - val_accuracy: 0.9875
Epoch 4/15
419/419 [==============================] - 151s 361ms/step - loss: 0.0194 - accuracy: 0.9949 - val_loss: 0.0189 - val_accuracy: 0.9948
Epoch 5/15
419/419 [==============================] - 150s 358ms/step - loss: 0.0070 - accuracy: 0.9984 - val_loss: 0.1011 - val_accuracy: 0.9765
Epoch 6/15
419/419 [==============================] - 150s 358ms/step - loss: 0.0782 - accuracy: 0.9706 - val_loss: 0.0927 - val_accuracy: 0.9652
Epoch 7/15
419/419 [==============================] - 153s 366ms/step - loss: 0.0537 - accuracy: 0.9830 - val_loss: 0.0702 -

## Evaluating the model

In [ ]:
loss, acc = model_2.evaluate(X_test, y_test)